# Programmatic example with NetCDF input

In [ ]:
%%javascript
// leave this in to disable autoscroll in Jupyter notebook
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

## Imports

In [ ]:
import fcpy

## Load data

In [ ]:
# the `load_dataset' option is currently unavalable due to data handling system move.
# ds = fcpy.load_dataset(model='atmospheric-model', var_names=['2t', 'q', 'sst'], levels=list(range(1, 10)))

# The `data` folder contains two sample NetCDF files.
# Here we load specific humidity from CAMS at 32 bits
fpath = "../data/*_q_*.nc"

ds = fcpy.open_dataset(fpath)
ds = ds[["q"]]  # Select only q as this dataset contains more vars...
ds

## Define and run experiment

In [ ]:
suite = fcpy.Suite(
    ds,
    baseline=fcpy.Float(bits=32),
    compressors=[fcpy.LinQuantization(), fcpy.Round()],
    metrics=[fcpy.Difference, fcpy.AbsoluteError],
    bits=[13],
    max_chunk_size_bytes=451 * 900 * 6,
    skip_histograms=False,
)

## Lineplot: evaluate the effect of bits

In [ ]:
suite.lineplot(fcpy.AbsoluteError, reduction="max")

## Boxplot: evaluate statistical characteristics of errors

In [ ]:
bits = 13
suite.boxplot(metric=fcpy.Difference, compressor="LinQuantization", bits=bits)
suite.boxplot(metric=fcpy.Difference, compressor="Round", bits=bits)

## Histogram: evaluate statistical characteristics of errors

In [ ]:
bits = 13
suite.histplot(metric=fcpy.Difference, compressor="LinQuantization", bits=bits)
suite.histplot(metric=fcpy.Difference, compressor="Round", bits=bits)

## Spatial plots: evaluate the spatial distribution of errors

In [ ]:
# Here we compare the spatial change of specific humidity
# by rounding values to 8 bits
fcpy.spatialplot(
    ds=ds,
    baseline=fcpy.Float(bits=32),
    var_name="q",
    compressor=fcpy.Round(bits=6),
    metric=fcpy.Difference,
    latitude=0,
    longitude=0,
    lev=1,
    third_dim="lev",
)